# GQA balancing

Intuitively, the downsampling parameters should be estimatable and the balancing should be reverse engineerable:

```
for each global group: downsample
for each local group: downsample
```

Downsampling for each answer with normalized count
1. for sure, $f_{min} \le \frac{c_{i+1}}{c_i} \le f_{max} \forall a_i, a_{i+1}$
2. $\frac{\sum_{j \le i} c_j}{1 - \sum_{j \le i} c_j} \le b$ for the 'head' of the distribution up to $i$, which is iteratively increased
    * probably we can't successfully guess the $i$, so no chance

Problematic steps afterwards: 
* there is further downsampling occuring, which means that the parameters can't be told for sure.
* We split the dataset into 70% train, 10% validation, 10% test and 10% challenge, making sure that all the questions about a given image appear in the same split.

Purported and infered postconditions:
* this ensures that the relative frequency-based answer ranking stays the same (p. 6)
* we iterate over the answers of that group in decreasing frequency order and reweight P's head up to the current iteration to make it more comparable to the tail size

In [1]:
from pathlib import Path
import json
import pandas as pd
import matplotlib.pyplot as plt
from collections import Counter
import plotly.express as px
import plotly.graph_objects as go
import numpy as np

In [2]:
show_big_figures = True

## Loading GQA

It takes quiet some time to execute the next cell (on my machine 17min):

In [3]:
gqa_data_path = Path('ver1.2/')

# balanced questions
gqa_train_balanced_questions = pd.DataFrame(json.load(open(Path(gqa_data_path / ('train_' + 'balanced_' + 'questions.json'))))).T
gqa_val_balanced_questions = pd.DataFrame(json.load(open(Path(gqa_data_path / ('val_' + 'balanced_' + 'questions.json'))))).T
gqa_testdev_balanced_questions = pd.DataFrame(json.load(open(Path(gqa_data_path / ('testdev_' + 'balanced_' + 'questions.json'))))).T

gqa_testdev_balanced_questions_test = json.load(open(Path(gqa_data_path / ('testdev_' + 'balanced_' + 'questions.json'))))

# all questions
gqa_train_all_questions_file_paths = [file for file in Path(gqa_data_path / 'train_all_questions').glob('*.json')]
gqa_train_all_questions = pd.DataFrame(json.load(open(gqa_train_all_questions_file_paths[0]))).T
for file in gqa_train_all_questions_file_paths[1:]:
    gqa_train_all_questions = pd.concat([gqa_train_all_questions, pd.DataFrame(json.load(open(file))).T])
gqa_val_all_questions = pd.DataFrame(json.load(open(Path(gqa_data_path / ('val_' + 'all_' + 'questions.json'))))).T
gqa_testdev_all_questions = pd.DataFrame(json.load(open(Path(gqa_data_path / ('testdev_' + 'all_' + 'questions.json'))))).T

gqa_val_all_questions_test = json.load(open(Path(gqa_data_path / ('val_' + 'all_' + 'questions.json'))))

In [4]:
gqa_train_balanced_questions['datasplit'] = 'train'
gqa_val_balanced_questions['datasplit'] = 'val'
gqa_testdev_balanced_questions['datasplit'] = 'testdev'

gqa_train_all_questions['datasplit'] = 'train'
gqa_val_all_questions['datasplit'] = 'val'
gqa_testdev_all_questions['datasplit'] = 'testdev'

## Filling the DataFrames

### Concatinating and Calculating

In [5]:
gqa_question_stats_balanced = pd.concat([gqa_train_balanced_questions[['answer', 'groups', 'imageId', 'question', 'entailed', 'equivalent']],
                                         gqa_val_balanced_questions[['answer', 'groups', 'imageId', 'question', 'entailed', 'equivalent']],
                                         gqa_testdev_balanced_questions[['answer', 'groups', 'imageId', 'question', 'entailed', 'equivalent']],])
gqa_question_stats_balanced.loc[slice(None),'local_question_group'] = gqa_question_stats_balanced['groups'].apply(lambda x: x['local'])
gqa_question_stats_balanced.loc[slice(None),'local_question_group_clean'] = gqa_question_stats_balanced['groups'].apply(lambda x: x['local'].split('-')[-1].split(',')[0] if type(x['local']) is str else None)
gqa_question_stats_balanced.loc[slice(None),'global_question_group'] = gqa_question_stats_balanced['groups'].apply(lambda x: x['global'])
gqa_question_stats_balanced.head(5)

answer                                             groups  imageId  \
02930152     yes           {'global': None, 'local': '06-sky_dark'}  2354786   
07333408    pipe            {'global': '', 'local': '14-wall_on,s'}  2375429   
07333405      no           {'global': None, 'local': '06-pipe_red'}  2375429   
15736264   large      {'global': 'size', 'local': '10c-clock_size'}  2368326   
111007521   girl  {'global': 'person', 'local': '14-shirt_wearin...  2331819   

                                    question  \
02930152                    Is the sky dark?   
07333408          What is on the white wall?   
07333405                   Is that pipe red?   
15736264   Is the tall clock small or large?   
111007521            Who is wearing a shirt?   

                                                    entailed   equivalent  \
02930152   [02930160, 02930158, 02930159, 02930154, 02930...   [02930152]   
07333408                                                  []   [07333408]   
07333405                                          [07333406]   [07333405]   
15736264   [15736259, 15736258, 15736267, 15736253, 15736...   [15736264]   
111007521                                                 []  [111007521]   

          local_question_group local_question_group_clean  \
02930152           06-sky_dark                   sky_dark   
07333408          14-wall_on,s                    wall_on   
07333405           06-pipe_red                   pipe_red   
15736264        10c-clock_size                 clock_size   
111007521   14-shirt_wearing,s              shirt_wearing   

          global_question_group  
02930152                   None  
07333408                         
07333405                   None  
15736264                   size  
111007521                person

In [6]:
gqa_question_stats_all = pd.concat([gqa_train_all_questions[['answer', 'groups', 'imageId', 'question', 'entailed', 'equivalent']],
                                    gqa_val_all_questions[['answer', 'groups', 'imageId', 'question', 'entailed', 'equivalent']],
                                    gqa_testdev_all_questions[['answer', 'groups', 'imageId', 'question', 'entailed', 'equivalent']],])
gqa_question_stats_all.loc[slice(None),'local_question_group'] = gqa_question_stats_all['groups'].apply(lambda x: x['local'])
gqa_question_stats_all.loc[slice(None),'local_question_group_clean'] = gqa_question_stats_all['groups'].apply(lambda x: x['local'].split('-')[-1].split(',')[0] if type(x['local']) is str else None)
gqa_question_stats_all.loc[slice(None),'global_question_group'] = gqa_question_stats_all['groups'].apply(lambda x: x['global'])
gqa_question_stats_all.head(5)

answer                                           groups  imageId  \
08519876     no        {'global': None, 'local': '04-chair_tan'}  2317174   
08519877     no        {'global': None, 'local': '04-chair_tan'}  2317174   
08519870    yes        {'global': None, 'local': '06-chair_red'}  2317174   
08519871    red  {'global': 'color', 'local': '10q-chair_color'}  2317174   
08519872     no      {'global': None, 'local': '06-chair_beige'}  2317174   

                                                   question  \
08519876        Is there a chair that is tan in this scene?   
08519877   Are there chairs in the photograph that are tan?   
08519870  Does the chair to the left of the person look ...   
08519871                          Which color is the chair?   
08519872                                Is the chair beige?   

                                                   entailed  \
08519876                                         [08519877]   
08519877                                         [08519876]   
08519870  [08519869, 08519868, 08519880, 08519872, 08519...   
08519871  [08519869, 08519868, 08519880, 08519872, 08519...   
08519872                               [08519873, 08519874]   

                    equivalent local_question_group  \
08519876            [08519876]         04-chair_tan   
08519877            [08519877]         04-chair_tan   
08519870            [08519870]         06-chair_red   
08519871            [08519871]      10q-chair_color   
08519872  [08519872, 08519873]       06-chair_beige   

         local_question_group_clean global_question_group  
08519876                  chair_tan                  None  
08519877                  chair_tan                  None  
08519870                  chair_red                  None  
08519871                chair_color                 color  
08519872                chair_beige                  None

### helper functions

In [7]:
# calculate the ratio between consecutive answers
def calculate_consec_ratio(group):
    group['consec_ratio'] = group['normalized_count'] / group['normalized_count'].shift(1)
    return group

# add a column for the answer, with the value indicating the position in the group
def calculate_position(group):
    group['answer_position'] = range(1, len(group) + 1)
    return group

# make a new column of the head probability weight, which takes the cumsum of the normalized_count so far for its group
def calculate_cumsum(group):
    group['head_prob_weight'] = group['normalized_count'].cumsum()
    return group

In [8]:
def estimate_parameter(df, level, filter_threshold=1000, conditionals=None, plot=True, answers_filter_threshold=15, dataset_type='balanced'):
    """
    Try to estimate and plot the paramters of the balancing.
    Only use types with many answers.
    
    level: local (answer type) or global (question group)
    filter_threshold: the minimum number of answers for a group to be included OR
    conditionals: a list of conditionals to filter the df if the level is local, overwrites the filter_threshold
    plot: whether to plot the results
    """
    if 'local' in level and not conditionals is not None:
        column = 'local_question_group_clean'
    elif 'local' in level and conditionals:
        column = 'local_question_group'
    elif 'global' in level:
        column = 'global_question_group'
    else:  
        raise ValueError('level must be local or global')

    suffix = ""
    if conditionals is not None and 'local' in level:
        # filter the df to only include the conditionals
        group_counts = df[df['local_question_group'].isin(conditionals)][column].value_counts()
        df_filtered = df[df[column].isin(group_counts.index)]
        suffix = "conditionals"
    else:
        # filter the df to only include groups with many answers
        group_counts = df[column].value_counts()
        group_counts = group_counts[group_counts > filter_threshold]
        df_filtered = df[df[column].isin(group_counts.index)]
        suffix = "filterthreshold"

    # calculate the normalized count of each type
    group_counts = df_filtered.groupby(by=column)['answer'].value_counts(normalize=True)
    group_counts = pd.DataFrame(group_counts)
    group_counts = group_counts.rename(columns={group_counts.columns[0]: 'normalized_count'})

    # calculate the ratio between consecutive answers
    group_counts_ratio = group_counts.groupby(level=0).apply(calculate_consec_ratio).reset_index(level=0, drop=True) # TODO: function not working

    # reconstruct the column
    group_counts_ratio[column] = df_filtered.groupby(by=column)['answer'].value_counts(normalize=True).index.get_level_values(0)

    # add a column indicating the position of the group in the df
    group_counts_ratio['group_position'] = group_counts_ratio.index
    group_counts_ratio['group_position'] = group_counts_ratio['group_position'].apply(lambda x: x[0])
    group_counts_ratio['group_position'] = group_counts_ratio['group_position'].astype('category')
    group_counts_ratio['group_position'] = group_counts_ratio['group_position'].cat.codes

    # add a column with a positional index within the group
    group_counts_ratio['answer_position'] = group_counts_ratio.groupby(level=0).cumcount()

    if plot:
        # filter the first x answers
        group_counts_ratio_filtered = group_counts_ratio[group_counts_ratio['answer_position'] <= answers_filter_threshold]

        # scatter plot of the consecutive answer ratio, with the group position as the x-axis and the answer position as the color
        fig = px.scatter(group_counts_ratio_filtered, x=column, y='consec_ratio', color='answer_position', title=f'Consecutive answer ratio for {dataset_type} questions with {suffix}')
        fig.write_image(f'results/BAL_{dataset_type}_{level}_{suffix}_consecutive_ratio.png', width=1000, height=800)
        if show_big_figures:
            fig.show()

    # add a column of the cumsum of the probablities so far for each group
    group_counts_ratio = group_counts_ratio.groupby(level=0).apply(calculate_cumsum).reset_index(level=0, drop=True)

    # add a colum of the head2tail probability weight, which takes the cumsum of the normalized_count so far for its group
    group_counts_ratio['head2tail'] = group_counts_ratio['head_prob_weight'].apply(lambda x: x / (1 - x) if x != 1. else np.nan)

    if plot:
        # filter the first x answers
        group_counts_ratio_filtered = group_counts_ratio[group_counts_ratio['answer_position'] <= answers_filter_threshold]

        # scatter plot of the head2tail, answer_type_clean as the x-axis and with the position in group as the color
        fig = px.scatter(group_counts_ratio_filtered, x=column, y='head2tail', color='answer_position', title=f'Head count weight to tail for {dataset_type} questions with {suffix}') # group_counts_ratio_filtered

        # the value easily explodes, so the y-axis is truncated to [0, 10]
        fig.update_layout(yaxis_range=[0, 10])
        fig.write_image(f'results/BAL_{dataset_type}_{level}_{suffix}_head2tail.png', width=1000, height=800)
        if show_big_figures:
            fig.show()
    
    return group_counts_ratio

## Estimating the Parameters (ReadMe 2.)

Taking only groups with at least 1000 answers, through construction of the algo, especially for the `local question group` (`answer type`), the parameters of the downsampling should be directly spotable.

In [48]:
frequent_conditionals = gqa_question_stats_all['local_question_group'].value_counts().head(50)
frequent_conditionals = list(frequent_conditionals.index)
frequent_conditionals

['03-fence',
 '03-car',
 '09existOr-car_fence',
 '03-glasses',
 '03-helmet',
 '03-chair',
 '02q-place',
 '09existOr-fence_helmet',
 '03-bag',
 '03-window',
 '02c-location',
 '03-bus',
 '01-location_indoors',
 '01-location_outdoors',
 '09existOr-fence_glasses',
 '03-clock',
 '13-man_woman',
 '13-woman_man',
 '03-mirror',
 '11q-furniture',
 '09existOr-door_window',
 '06-sky_blue',
 '03-boy',
 '09existAnd-door_window',
 '04-grass_brown',
 '11q-animal',
 '03-door',
 '03-woman',
 '09existOr-bus_car',
 '03-grass',
 '09existOr-bus_fence',
 '13-man_bag',
 '03-lamp',
 '03-picture',
 '13-man_helmet',
 '04-grass_green',
 '03-plate',
 '10q-shirt_color',
 '13-man_chair',
 '03-table',
 '09existOr-boy_fence',
 '03-umbrella',
 '04-table_wood',
 '02c-place',
 '06-sky_white',
 '10q-sky_color',
 '03-train',
 '02q-weather',
 '10c-sky_color',
 '13-man_fence']

In [31]:
gqa_question_stats_balanced[gqa_question_stats_balanced['local_question_group'] == '11q-furniture']['answer'].value_counts()


answer
table                   863
bed                     677
desk                    468
chair                   463
couch                   328
shelf                   305
cabinet                 223
sofa                    128
cabinets                112
cupboard                 42
shelves                  40
drawer                   34
bookshelf                32
chairs                   30
computer desk            26
closet                   22
dresser                  18
bookcase                 17
tv stand                 16
coffee table             15
dining table             15
entertainment center     14
drawers                  10
tables                    8
medicine cabinet          6
armchair                  6
nightstand                5
beds                      4
office chair              4
side table                2
cupboards                 2
bar stools                2
wardrobe                  2
bookshelves               2
Name: count, dtype: int64

In [49]:
# get the balancing based on the conditionals
local_group_counts_ratio_balanced_conditionals = estimate_parameter(gqa_question_stats_balanced, 'local', conditionals=frequent_conditionals, dataset_type='balanced')

In [50]:
local_group_counts_ratio_all_conditionals = estimate_parameter(gqa_question_stats_all, 'local', conditionals=frequent_conditionals, dataset_type='all')

In [23]:
local_group_counts_ratio_balanced = estimate_parameter(gqa_question_stats_balanced, 'local', answers_filter_threshold=20, dataset_type='balanced')

There might be sth like a bound at $0.5$ for the consecutive ratio, but for many it does not work... for the head2tail I can see nothing like a bound.

In [24]:
local_group_counts_ratio_all = estimate_parameter(gqa_question_stats_all, 'local', dataset_type='all')

## Relative Frequency Based Ranking (ReadMe 3.) - conditionals

As the downsampling seems to be based on the conditionals, get the statistics there:

In [25]:
local_group_counts_ratio_balanced_conditionals = estimate_parameter(gqa_question_stats_balanced, 'local', conditionals=frequent_conditionals,
                                                                    dataset_type='balanced', plot=False)
local_group_counts_ratio_all_conditionals = estimate_parameter(gqa_question_stats_all, 'local', conditionals=frequent_conditionals,
                                                               dataset_type='all', plot=False)

local_group_counts_ratio_everything_conditionals = local_group_counts_ratio_balanced_conditionals.join(local_group_counts_ratio_all_conditionals,
                                                                                                       rsuffix='_all', lsuffix='_balanced')

In [26]:
local_group_counts_ratio_everything_conditionals[['normalized_count_balanced', 'answer_position_balanced',
                                                              'normalized_count_all', 'answer_position_all']].sort_values(by='answer_position_all', ascending=True)

normalized_count_balanced  \
local_question_group answer                                   
01-location_indoors  no                            0.504689   
03-bus               no                            0.550633   
03-chair             no                            0.508557   
03-clock             no                            0.502825   
03-door              yes                           0.478903   
...                                                     ...   
02q-place            coffee shop                   0.000448   
                     cemetery                      0.000224   
                     pub                           0.000336   
                     lounge                        0.000224   
                     pizza shop                    0.000224   

                                  answer_position_balanced  \
local_question_group answer                                  
01-location_indoors  no                                  0   
03-bus               no                                  0   
03-chair             no                                  0   
03-clock             no                                  0   
03-door              yes                                 1   
...                                                    ...   
02q-place            coffee shop                        83   
                     cemetery                           87   
                     pub                                85   
                     lounge                             88   
                     pizza shop                         89   

                                  normalized_count_all  answer_position_all  
local_question_group answer                                                  
01-location_indoors  no                       0.808118                    0  
03-bus               no                       0.862546                    0  
03-chair             no                       0.786122                    0  
03-clock             no                       0.851224                    0  
03-door              yes                      0.563351                    0  
...                                                ...                  ...  
02q-place            coffee shop              0.000184                   85  
                     cemetery                 0.000123                   86  
                     pub                      0.000123                   87  
                     lounge                   0.000082                   88  
                     pizza shop               0.000082                   89  

[250 rows x 4 columns]

In [34]:
local_group_counts_ratio_everything_conditionals[(local_group_counts_ratio_everything_conditionals['answer_position_all'] <20) & 
                                                 (local_group_counts_ratio_everything_conditionals['answer_position_balanced'] != local_group_counts_ratio_everything_conditionals['answer_position_all'])][['normalized_count_balanced', 'answer_position_balanced', 'normalized_count_all', 'answer_position_all']]

normalized_count_balanced  \
local_question_group answer                                
02q-place            street                     0.090471   
                     ocean                      0.066984   
                     road                       0.051289   
                     park                       0.034978   
                     pavement                   0.032511   
...                                                  ...   
13-woman_man         right                      0.261523   
                     no                         0.258517   
                     yes                        0.190381   
                     behind                     0.008016   
                     front                      0.007014   

                               answer_position_balanced  normalized_count_all  \
local_question_group answer                                                     
02q-place            street                           1              0.105155   
                     ocean                            2              0.054750   
                     road                             3              0.122292   
                     park                             5              0.040996   
                     pavement                         6              0.024946   
...                                                 ...                   ...   
13-woman_man         right                            1              0.072132   
                     no                               2              0.364671   
                     yes                              3              0.489279   
                     behind                           4              0.001896   
                     front                            5              0.002079   

                               answer_position_all  
local_question_group answer                         
02q-place            street                      2  
                     ocean                       5  
                     road                        1  
                     park                        6  
                     pavement                    7  
...                                            ...  
13-woman_man         right                       2  
                     no                          1  
                     yes                         0  
                     behind                      5  
                     front                       4  

[62 rows x 4 columns]

In [40]:
# which is the worst group? weight the difference by 3 if the answer_position_balanced is less then 10, 2 if less than 30, 1 if less than 30
local_group_counts_ratio_everything_conditionals['weight'] = local_group_counts_ratio_everything_conditionals['answer_position_all'].apply(lambda x: 3 if x < 10 else (2 if x < 30 else 1))
local_group_counts_ratio_everything_conditionals['difference_weighted'] = local_group_counts_ratio_everything_conditionals['weight'] * abs(local_group_counts_ratio_everything_conditionals['answer_position_balanced'] - local_group_counts_ratio_everything_conditionals['answer_position_all'])

local_group_counts_ratio_everything_conditionals

normalized_count_balanced  \
local_question_group answer                                
01-location_indoors  no                         0.504689   
                     yes                        0.495311   
01-location_outdoors yes                        0.510836   
                     no                         0.489164   
02c-location         outdoors                   0.554244   
...                                                  ...   
13-woman_man         right                      0.261523   
                     no                         0.258517   
                     yes                        0.190381   
                     behind                     0.008016   
                     front                      0.007014   

                               consec_ratio_balanced  \
local_question_group answer                            
01-location_indoors  no                          NaN   
                     yes                    0.981419   
01-location_outdoors yes                         NaN   
                     no                     0.957576   
02c-location         outdoors                    NaN   
...                                              ...   
13-woman_man         right                  0.952555   
                     no                     0.988506   
                     yes                    0.736434   
                     behind                 0.042105   
                     front                  0.875000   

                              local_question_group_balanced  \
local_question_group answer                                   
01-location_indoors  no                 01-location_indoors   
                     yes                01-location_indoors   
01-location_outdoors yes               01-location_outdoors   
                     no                01-location_outdoors   
02c-location         outdoors                  02c-location   
...                                                     ...   
13-woman_man         right                     13-woman_man   
                     no                        13-woman_man   
                     yes                       13-woman_man   
                     behind                    13-woman_man   
                     front                     13-woman_man   

                               group_position_balanced  \
local_question_group answer                              
01-location_indoors  no                              0   
                     yes                             0   
01-location_outdoors yes                             1   
                     no                              1   
02c-location         outdoors                        2   
...                                                ...   
13-woman_man         right                          27   
                     no                             27   
                     yes                            27   
                     behind                         27   
                     front                          27   

                               answer_position_balanced  \
local_question_group answer                               
01-location_indoors  no                               0   
                     yes                              1   
01-location_outdoors yes                              0   
                     no                               1   
02c-location         outdoors                         0   
...                                                 ...   
13-woman_man         right                            1   
                     no                               2   
                     yes                              3   
                     behind                           4   
                     front                            5   

                               head_prob_weight_balanced  head2tail_balanced  \
local_question_group answer                                                    
01-location_indoor

In [42]:
# highest difference_weighted groupedby answer_type_clean
local_group_counts_ratio_everything_conditionals.groupby('local_question_group')['difference_weighted'].sum().sort_values(ascending=False)

local_question_group
02q-place                  551
11q-animal                 179
11q-furniture               50
13-woman_man                30
13-man_woman                30
03-bag                       6
09existOr-fence_helmet       6
09existOr-fence_glasses      6
03-door                      6
03-grass                     6
09existOr-car_fence          6
09existOr-bus_car            6
09existAnd-door_window       6
06-sky_blue                  6
04-grass_brown               0
09existOr-door_window        0
01-location_indoors          0
03-woman                     0
01-location_outdoors         0
03-mirror                    0
03-helmet                    0
03-fence                     0
03-clock                     0
03-chair                     0
03-bus                       0
03-boy                       0
02c-location                 0
03-window                    0
Name: difference_weighted, dtype: int64

### How it was actually sampled

In [43]:
column = '02q-place'

In [44]:
# get all the questions that were excluded from all questions when it was downsampled to be the balanced set
balanced_filtered_by_column = gqa_question_stats_balanced[gqa_question_stats_balanced['local_question_group'] == column]
balanced_qids_filtered_by_column = set(balanced_filtered_by_column.index)
print(f"The number of questions of column {column} is {len(balanced_qids_filtered_by_column)}")

all_filtered_by_column = gqa_question_stats_all[gqa_question_stats_all['local_question_group'] == column]
all_qids_filtered_by_column = set(all_filtered_by_column.index)
print(f"The number of questions of column {column} is {len(all_qids_filtered_by_column)}")

# get the qids that were excluded from the balanced set
excluded_qids = all_qids_filtered_by_column.difference(balanced_qids_filtered_by_column)

# print the questions excluded from all
all_filtered_by_column.loc[list(excluded_qids)]

The number of questions of column 02q-place is 17840
The number of questions of column 02q-place is 48785


answer                                     groups  imageId  \
04594688     road   {'global': 'road', 'local': '02q-place'}  2344715   
16448988    field  {'global': 'place', 'local': '02q-place'}  2345015   
17573667     road   {'global': 'road', 'local': '02q-place'}  2392625   
14936132    field  {'global': 'place', 'local': '02q-place'}  2344376   
01848024    field  {'global': 'place', 'local': '02q-place'}  2398383   
...           ...                                        ...      ...   
0777212      road   {'global': 'road', 'local': '02q-place'}  2395208   
0067022      road   {'global': 'road', 'local': '02q-place'}  2369970   
091017017   store  {'global': 'place', 'local': '02q-place'}  2347055   
18899534   street  {'global': 'place', 'local': '02q-place'}  2367938   
02751194    ocean  {'global': 'place', 'local': '02q-place'}  2370732   

                             question  \
04594688           Which place is it?   
16448988           Which place is it?   
17573667    What kind of place is it?   
14936132          What place is this?   
01848024      What place is pictured?   
...                               ...   
0777212             What place is it?   
0067022    What is the photo showing?   
091017017          Which place is it?   
18899534      What place is pictured?   
02751194         What place is shown?   

                                                    entailed  \
04594688                                [04594686, 04594687]   
16448988   [16448990, 16448991, 16448992, 16448989, 16448...   
17573667                                [17573666, 17573668]   
14936132   [14936133, 14936134, 14936135, 14936136, 14936...   
01848024            [01848025, 01848026, 01848027, 01848028]   
...                                                      ...   
0777212                                   [0777213, 0777211]   
0067022                                            [0067023]   
091017017  [091017020, 091017015, 091017016, 091017019, 0...   
18899534                                [18899533, 18899535]   
02751194                                          [02751195]   

                     equivalent local_question_group  \
04594688             [04594688]            02q-place   
16448988             [16448988]            02q-place   
17573667   [17573667, 17573666]            02q-place   
14936132             [14936132]            02q-place   
01848024             [01848024]            02q-place   
...                         ...                  ...   
0777212      [0777212, 0777211]            02q-place   
0067022               [0067022]            02q-place   
091017017           [091017017]            02q-place   
18899534   [18899533, 18899534]            02q-place   
02751194             [02751194]            02q-place   

          local_question_group_clean global_question_group  
04594688                       place                  road  
16448988                       place                 place  
17573667                       place                  road  
14936132                       place                 place  
01848024                       place                 place  
...                              ...                   ...  
0777212                        place                  road  
0067022                        place                  road  
091017017                      place                 place  
18899534                       place                 place  
02751194                       place                 place  

[30945 rows x 9 columns]

In [45]:
# plot the answer distribution change with a plotly stacked histogram, counting the number of ansers in balanced_filtered_by_column and all_filtered_by_column
fig = go.Figure()
fig.add_trace(go.Histogram(x=all_filtered_by_column['answer'], name='all'))
fig.add_trace(go.Histogram(x=balanced_filtered_by_column['answer'], name='balanced'))

order = list(all_filtered_by_column['answer'].value_counts().index)
fig.update_xaxes(categoryorder='array', categoryarray= order)
fig.update_layout(barmode='overlay', title=f'Answer count distribution for {column} questions')

fig.write_image(f'results/BAL_{column}_answer_distribution.png', width=1500, height=600)
if show_big_figures:
    fig.show()

In [46]:
balanced_filtered_by_column_vc = balanced_filtered_by_column['answer'].value_counts()
all_filtered_by_column_vc = all_filtered_by_column['answer'].value_counts()

balanced_filtered_by_column_vc = balanced_filtered_by_column_vc / all_filtered_by_column_vc

# set all values of all_filtered_by_column_vc to 1
all_filtered_by_column_vc = all_filtered_by_column_vc / all_filtered_by_column_vc

In [47]:
# plot a plotly stacked bar chart with balanced_filtered_by_column_vc, all_filtered_by_column_vc
fig = go.Figure()
fig.add_trace(go.Bar(x=all_filtered_by_column_vc.index, y=all_filtered_by_column_vc.values, name='all'))
fig.add_trace(go.Bar(x=balanced_filtered_by_column_vc.index, y=balanced_filtered_by_column_vc.values, name='balanced'))

fig.update_xaxes(categoryorder='array', categoryarray= order)
fig.update_layout(barmode='overlay', title=f'Answer ratio distribution for {column} questions')

fig.write_image(f'results/BAL_{column}_answer_distribution_ratio.png', width=2000, height=600)
if show_big_figures:
    fig.show()

## Relative Frequency Based Ranking (ReadMe 3.) - OLD VERSION

This version of the code is based on the assumption that the downsampling was performed on a cleaned version of the local groups, but that seems to be wrong.

In [11]:
local_group_counts_ratio_balanced = estimate_parameter(gqa_question_stats_balanced, 'local', plot=False,  answers_filter_threshold=np.inf)
local_group_counts_ratio_all = estimate_parameter(gqa_question_stats_all, 'local', plot=False,  answers_filter_threshold=np.inf)

local_group_counts_ratio_everything = local_group_counts_ratio_balanced.join(local_group_counts_ratio_all, rsuffix='_all', lsuffix='_balanced')

In [12]:
local_group_counts_ratio_everything.loc['woman_wearing'].head(30)[['normalized_count_balanced', 'answer_position_balanced',
                                                              'normalized_count_all', 'answer_position_all']].sort_values(by='answer_position_all', ascending=True)

normalized_count_balanced  answer_position_balanced  \
answer                                                             
shirt                         0.089286                         1   
dress                         0.101562                         0   
jacket                        0.077009                         2   
glasses                       0.058036                         3   
pants                         0.053571                         4   
hat                           0.053292                         5   
jeans                         0.049665                         7   
coat                          0.050223                         6   
skirt                         0.041016                         8   
sweater                       0.034319                         9   
shorts                        0.027344                        10   
tank top                      0.023996                        11   
wetsuit                       0.018415                        13   
necklace                      0.017020                        14   
scarf                         0.018415                        12   
bikini                        0.013393                        19   
cap                           0.013672                        18   
t-shirt                       0.014230                        16   
earring                       0.012556                        20   
blouse                        0.014230                        15   
watch                         0.013951                        17   
outfit                        0.011998                        21   
ring                          0.011998                        22   
eye glasses                   0.010603                        24   
suit                          0.009487                        26   
sandals                       0.009208                        27   
bracelet                      0.010045                        25   
swimsuit                      0.010882                        23   
apron                         0.007533                        29   
boots                         0.007812                        28   

             normalized_count_all  answer_position_all  
answer                                                  
shirt                    0.226518                    0  
dress                    0.081848                    1  
jacket                   0.065992                    2  
glasses                  0.054213                    3  
pants                    0.045757                    4  
hat                      0.040018                    5  
jeans                    0.039112                    6  
coat                     0.038055                    7  
skirt                    0.031410                    8  
sweater                  0.028239                    9  
shorts                   0.021897                   10  
tank top                 0.018423                   11  
wetsuit                  0.015856                   13  
necklace                 0.013289                   14  
scarf                    0.012534                   16  
bikini                   0.011024                   17  
cap                      0.010873                   18  
t-shirt                  0.010722                   19  
earring                  0.010420                   21  
blouse                   0.010269                   22  
watch                    0.010118                   23  
outfit                   0.009816                   24  
ring                     0.008910                   26  
eye glasses              0.008306                   27  
suit                     0.008004                   28  
sandals                  0.007400                   29  
bracelet                 0.007098                   30  
swimsuit                 0.006947                   32  
apron                    0.005738                   33  
boots                    0.005587                   34

This shows that there is quiet a change in the relative frequency-based ranking of the answers, at least for this `local question group`.

In [13]:
# get some rows in which answer_position != answer_position_all and where the original answer position is not too high
local_group_counts_ratio_everything[(local_group_counts_ratio_everything['answer_position_all'] <20) & (local_group_counts_ratio_everything['answer_position_balanced'] != local_group_counts_ratio_everything['answer_position_all'])][['normalized_count_balanced', 'answer_position_balanced', 'normalized_count_all', 'answer_position_all']].sample(20)

normalized_count_balanced  \
local_question_group_clean answer                                   
shelf_on                   container                     0.006415   
street_on                  train                         0.005333   
cap_wearing                dog                           0.006050   
vehicle                    wagon                         0.018491   
shirt_wearing              surfer                        0.005503   
pants_color                light brown                   0.001513   
man_to the right of        boat                          0.001742   
sign_on                    letter                        0.053488   
hat_color                  maroon                        0.003900   
animal                     kitten                        0.010240   
pizza_on                   sausage                       0.028032   
plate_on                   salad                         0.023474   
boy_wearing                tie                           0.010295   
fence_in front of          train                         0.016069   
shelf_on                   bottle                        0.011227   
car_color                  blue                          0.116928   
jacket_color               white                         0.083696   
plate_on                   dessert                       0.018532   
water_in                   horse                         0.025063   
                           cow                           0.007519   

                                        answer_position_balanced  \
local_question_group_clean answer                                  
shelf_on                   container                          34   
street_on                  train                              22   
cap_wearing                dog                                17   
vehicle                    wagon                              11   
shirt_wearing              surfer                             13   
pants_color                light brown                        18   
man_to the right of        boat                               85   
sign_on                    letter                              2   
hat_color                  maroon                             16   
animal                     kitten                             12   
pizza_on                   sausage                            11   
plate_on                   salad                               7   
boy_wearing                tie                                19   
fence_in front of          train                              20   
shelf_on                   bottle                             14   
car_color                  blue                                2   
jacket_color               white                               6   
plate_on                   dessert                            12   
water_in                   horse                              12   
                           cow                                27   

                                        normalized_count_all  \
local_question_group_clean answer                              
shelf_on                   container                0.013679   
street_on                  train                    0.003619   
cap_wearing                dog                      0.005577   
vehicle                    wagon                    0.004189   
shirt_wearing              surfer                   0.002058   
pants_color                light brown              0.001325   
man_to the right of        boat                     0.013615   
sign_on                    letter                   0.044074   
hat_color                  maroon                   0.002709   
animal                     kitten                   0.004125   
pizza_on                   sausage                  0.018399   
plate_on                   salad                    0.013411   
boy_wearing                tie                      0.008638   
fence_in front of          train                    0.017325   


There are nearly 800 occurences of that, I just sample some.

In [14]:
# which is the worst group? weight the difference by 3 if the answer_position_balanced is less then 10, 2 if less than 30, 1 if less than 30
local_group_counts_ratio_everything['weight'] = local_group_counts_ratio_everything['answer_position_all'].apply(lambda x: 3 if x < 10 else (2 if x < 30 else 1))
local_group_counts_ratio_everything['difference_weighted'] = local_group_counts_ratio_everything['weight'] * abs(local_group_counts_ratio_everything['answer_position_balanced'] - local_group_counts_ratio_everything['answer_position_all'])

local_group_counts_ratio_everything

normalized_count_balanced  \
local_question_group_clean answer                                  
allanimals                 yes                          0.501440   
                           no                           0.498560   
animal                     cat                          0.243498   
                           dog                          0.179603   
                           horse                        0.123080   
...                                                          ...   
woman_wearing              shirts                       0.000279   
                           snowsuit                     0.000279   
                           suitcase                     0.000279   
                           table                        0.000279   
                           teddy bear                   0.000279   

                                       consec_ratio_balanced  \
local_question_group_clean answer                              
allanimals                 yes                           NaN   
                           no                       0.994257   
animal                     cat                           NaN   
                           dog                      0.737595   
                           horse                    0.685291   
...                                                      ...   
woman_wearing              shirts                   1.000000   
                           snowsuit                 1.000000   
                           suitcase                 1.000000   
                           table                    1.000000   
                           teddy bear               1.000000   

                                      local_question_group_clean_balanced  \
local_question_group_clean answer                                           
allanimals                 yes                                 allanimals   
                           no                                  allanimals   
animal                     cat                                     animal   
                           dog                                     animal   
                           horse                                   animal   
...                                                                   ...   
woman_wearing              shirts                           woman_wearing   
                           snowsuit                         woman_wearing   
                           suitcase                         woman_wearing   
                           table                            woman_wearing   
                           teddy bear                       woman_wearing   

                                       group_position_balanced  \
local_question_group_clean answer                                
allanimals                 yes                               0   
                           no                                0   
animal                     cat                               1   
                           dog                               1   
                           horse                             1   
...                                                        ...   
woman_wearing              shirts                           76   
                           snowsuit                         76   
                           suitcase                         76   
                           table                            76   
                           teddy bear                       76   

                                       answer_position_balanced  \
local_question_group_clean answer                                 
allanimals                 yes                                0   
                           no                                 1   
animal                     cat                                0   
                           dog                                1   
                           horse                          

In [15]:
# highest difference_weighted groupedby answer_type_clean
local_group_counts_ratio_everything.groupby('local_question_group_clean')['difference_weighted'].sum().sort_values(ascending=False)

local_question_group_clean
table_on               17571
man_to the right of     9278
man_in front of         8649
man_to the left of      7854
man_holding             6841
                       ...  
door_window                0
chair_hposition            0
car_hposition              0
bag_hposition              0
location_outdoors          0
Name: difference_weighted, Length: 77, dtype: int64

In [16]:
# make a histogram of the above with plotly
fig = px.histogram(local_group_counts_ratio_everything, x='difference_weighted', title='Ranking difference weighted by group')
fig.write_image('results/BAL_local_ranking_difference_weighted_by_group.png', width=1000, height=600)
if show_big_figures:
    fig.show()

For most the answers it's not massive, but for quiet some it is.

### Worst Cases

In [17]:
local_group_counts_ratio_everything.loc['table_on'][['answer_position_balanced', 'answer_position_all', 'normalized_count_balanced', 'normalized_count_all']]

answer_position_balanced  answer_position_all  \
answer                                                       
laptop                              0                    0   
glass                               1                    4   
bowl                                2                    8   
lamp                                3                    9   
cell phone                          4                    5   
...                               ...                  ...   
vitamins                          443                  454   
walkway                           444                  455   
wall                              445                  257   
water glass                       446                  456   
woman                             447                  457   

             normalized_count_balanced  normalized_count_all  
answer                                                        
laptop                        0.036761              0.063468  
glass                         0.035271              0.027569  
bowl                          0.025087              0.018184  
lamp                          0.024839              0.017832  
cell phone                    0.023845              0.025575  
...                                ...                   ...  
vitamins                      0.000248              0.000117  
walkway                       0.000248              0.000117  
wall                          0.000248              0.000469  
water glass                   0.000248              0.000117  
woman                         0.000248              0.000117  

[448 rows x 4 columns]

In [18]:
local_group_counts_ratio_everything.loc['man_to the right of'][['answer_position_balanced', 'answer_position_all',
                                                                'normalized_count_balanced', 'normalized_count_all']]

answer_position_balanced  answer_position_all  \
answer                                                     
chair                             0                    1   
car                               1                    0   
horse                             2                    2   
dog                               3                    5   
bus                               4                    3   
...                             ...                  ...   
trash bag                       226                  149   
trucks                          227                  135   
wardrobe                        228                  255   
wii                             229                   89   
zebra                           230                  101   

           normalized_count_balanced  normalized_count_all  
answer                                                      
chair                       0.099303              0.075494  
car                         0.069686              0.131654  
horse                       0.055168              0.043159  
dog                         0.044135              0.034173  
bus                         0.032520              0.039415  
...                              ...                   ...  
trash bag                   0.000581              0.000613  
trucks                      0.000581              0.000749  
wardrobe                    0.000581              0.000204  
wii                         0.000581              0.001430  
zebra                       0.000581              0.001225  

[231 rows x 4 columns]

#### How were the answers actually sampled?

As we have both `all` and `balanced` we should be able to see what was done (modulo a hopefully proportional thing which is the dataset split).

In [19]:
column = 'table_on'

In [20]:
# get all the questions that were excluded from all questions when it was downsampled to be the balanced set
balanced_filtered_by_column = gqa_question_stats_balanced[gqa_question_stats_balanced['local_question_group_clean'] == column]
balanced_qids_filtered_by_column = set(balanced_filtered_by_column.index)
print(f"The number of questions of column {column} is {len(balanced_qids_filtered_by_column)}")

all_filtered_by_column = gqa_question_stats_all[gqa_question_stats_all['local_question_group_clean'] == column]
all_qids_filtered_by_column = set(all_filtered_by_column.index)
print(f"The number of questions of column {column} is {len(all_qids_filtered_by_column)}")

# get the qids that were excluded from the balanced set
excluded_qids = all_qids_filtered_by_column.difference(balanced_qids_filtered_by_column)

# print the questions excluded from all
all_filtered_by_column.loc[list(excluded_qids)]

The number of questions of column table_on is 4026
The number of questions of column table_on is 8524


answer                                             groups  \
13910835       pizza  {'global': 'fast food', 'local': '15-table_on,s'}   
03495543       phone     {'global': 'device', 'local': '15-table_on,s'}   
05101484     speaker     {'global': 'device', 'local': '15-table_on,s'}   
13925177      napkin      {'global': 'thing', 'local': '14-table_on,s'}   
15350766      orange      {'global': 'color', 'local': '15-table_on,s'}   
...              ...                                                ...   
18946913      laptop     {'global': 'device', 'local': '15-table_on,s'}   
02585774        cake    {'global': 'dessert', 'local': '15-table_on,s'}   
18284033      kettle  {'global': 'cooking utensil', 'local': '14-tab...   
10608776  cell phone     {'global': 'device', 'local': '15-table_on,s'}   
12250272      laptop     {'global': 'device', 'local': '15-table_on,s'}   

          imageId                                           question  \
13910835  2403540              What is the food on the table called?   
03495543  2410346     What is the device that is on the black table?   
05101484  2412614             How is the device on the table called?   
13925177  2378920   What is on the table that looks black and brown?   
15350766  2362214  What is the fruit that is on the table made of...   
...           ...                                                ...   
18946913  2355792                       What device is on the table?   
02585774  2353242                      What dessert is on the table?   
18284033  2387027                 What is on the table made of wood?   
10608776  2404269                   What is the device on the table?   
12250272  2359411                       What device is on the table?   

                                                   entailed  \
13910835           [13910702, 13910842, 13910834, 13910836]   
03495543                     [03495549, 03495531, 03495542]   
05101484           [05101496, 05101495, 05101448, 05101485]   
13925177                     [13925185, 13925184, 13925178]   
15350766  [15350731, 15350775, 15350767, 15350765, 15350...   
...                                                     ...   
18946913                     [18946914, 18946911, 18946888]   
02585774                     [02585781, 02585773, 02585677]   
18284033  [18284042, 18284035, 18284034, 18284036, 18284...   
10608776  [10608765, 10608777, 10608767, 10608766, 10608...   
12250272           [12250269, 12250270, 12250243, 12250278]   

                    equivalent local_question_group  \
13910835            [13910835]        15-table_on,s   
03495543            [03495543]        15-table_on,s   
05101484  [05101484, 05101485]        15-table_on,s   
13925177            [13925177]        14-table_on,s   
15350766  [15350767, 15350766]        15-table_on,s   
...                        ...                  ...   
18946913            [18946913]        15-table_on,s   
02585774            [02585774]        15-table_on,s   
18284033            [18284033]        14-table_on,s   
10608776            [10608776]        15-table_on,s   
12250272            [12250272]        15-table_on,s   

         local_question_group_clean global_question_group  
13910835                   table_on             fast food  
03495543                   table_on                device  
05101484                   table_on                device  
13925177                   table_on                 thing  
15350766                   table_on                 color  
...                             ...                   ...  
18946913                   table_on                device  
02585774                   table_on               dessert  
18284033                   table_on       cooking utensil  
10608776                   table_on                device  
12250272                   table_on                device  

[4498 rows x 9 columns]

In [21]:
# plot the answer distribution change with a plotly stacked histogram, counting the number of ansers in balanced_filtered_by_column and all_filtered_by_column
fig = go.Figure()
fig.add_trace(go.Histogram(x=all_filtered_by_column['answer'], name='all'))
fig.add_trace(go.Histogram(x=balanced_filtered_by_column['answer'], name='balanced'))

order = list(all_filtered_by_column['answer'].value_counts().index)
fig.update_xaxes(categoryorder='array', categoryarray= order)
fig.update_layout(barmode='overlay', title=f'Answer count distribution for {column} questions')

fig.write_image('results/BAL_table_on_answer_distribution.png', width=1500, height=600)
if show_big_figures:
    fig.show()

In [22]:
balanced_filtered_by_column_vc = balanced_filtered_by_column['answer'].value_counts()
all_filtered_by_column_vc = all_filtered_by_column['answer'].value_counts()

balanced_filtered_by_column_vc = balanced_filtered_by_column_vc / all_filtered_by_column_vc

# set all values of all_filtered_by_column_vc to 1
all_filtered_by_column_vc = all_filtered_by_column_vc / all_filtered_by_column_vc

In [23]:
# plot a plotly stacked bar chart with balanced_filtered_by_column_vc, all_filtered_by_column_vc
fig = go.Figure()
fig.add_trace(go.Bar(x=all_filtered_by_column_vc.index, y=all_filtered_by_column_vc.values, name='all'))
fig.add_trace(go.Bar(x=balanced_filtered_by_column_vc.index, y=balanced_filtered_by_column_vc.values, name='balanced'))

fig.update_xaxes(categoryorder='array', categoryarray= order)
fig.update_layout(barmode='overlay', title=f'Answer ratio distribution for {column} questions')

fig.write_image('results/BAL_table_on_answer_distribution_ratio.png', width=2000, height=600)
if show_big_figures:
    fig.show()

* `cake` is strongly downsamples relative to `glass`
* some answers are downsampled to $0$, for `boat`, `bird`?